## search api

In [1]:
import urllib2
import urllib
import requests
from datetime import timedelta, datetime
from bs4 import BeautifulSoup
import cPickle as pickle
import re
import numpy as np
import pandas as pd

http://api.nytimes.com/svc/search/v2/articlesearch.json?q=books+review&fq=The+New+York+Times&begin_date=20150301&end_date=20150330&sort=newest&fl=web_url%2Cheadline%2Ckeywords&hl=true&api-key=38477d93e711afb3260ca02fcd5b1cdb%3A12%3A71777620

In [11]:
r = requests.get('http://api.nytimes.com/svc/search/v2/articlesearch.json?q=books+review&fq=The+New+York+Times&begin_date=20150301&end_date=20150330&sort=newest&fl=web_url%2Cheadline%2Ckeywords&hl=true&api-key=38477d93e711afb3260ca02fcd5b1cdb%3A12%3A71777620')
rjson = r.json()

In [14]:
type(rjson)

dict

## best sellers api

In [2]:
l = requests.get('http://api.nytimes.com/svc/books/v3/lists/names.json?api-key=ed91070ee5df688636a455cb3ad9cb72%3A2%3A71777620')

In [3]:
blist = l.json()

In [4]:
rlist = blist['results']

In [5]:
def extractdict(l, k):
    return [x[k].encode('utf-8') for x in l]

In [6]:
bestlist = extractdict(rlist, 'display_name')
pickle.dump(bestlist, open('listname.p', 'wb'))
#bestlist = picke.load( open('listname.p', 'wb'))


Get female and male first name lists

In [8]:
fem = pd.read_table('http://deron.meranda.us/data/census-dist-female-first.txt', sep='[ ]+',  header=None)
ma = pd.read_table('http://deron.meranda.us/data/census-dist-male-first.txt', sep='[ ]+',  header=None) 

In [9]:
perfem = fem[1].tolist()
permale = ma[1].tolist()
female = fem[0].str.lower().tolist()
male = ma[0].str.lower().tolist()
female2=[]
inmale = []
for f in range(len(female)):
    if female[f] in male:
        inmale.append(female[f])
        topop = male.index(female[f])
        if perfem[f] > permale[topop]:
            male.pop(topop)
            permale.pop(topop)
            female2.append(female[f])
    else:
        female2.append(female[f])
female = female2

Get literature genre

In [10]:
g = requests.get('http://en.wikipedia.org/wiki/List_of_literary_genres')
wg = g.text
gidx = wg.find('id="Genre')
aw = wg[gidx:wg.find('<h2>', gidx)]
l = re.findall('<li>(.+)</li>', aw)
#re.findall('title="(.+)"', aw)
genre = []
for i in l:
    if i[0] == '<':
        genre.append(re.findall('<a .+>(.+)</a>', i)[0].lower())
    else:
        genre.append(re.findall('(.+)&', i)[0].lower())

http://api.nytimes.com/svc/books/v3/lists/2014-01-15/Hardcover%20Fiction.json?api-key=ed91070ee5df688636a455cb3ad9cb72%3A2%3A71777620

In [11]:
bestlist = pickle.load( open('listname.p', 'rb'))
#hf = urllib.quote(bestlist[2])

In [289]:
#startDate = "01/01/09"
#date = datetime.strptime(startDate, "%m/%d/%y")

In [51]:
def get_list(d, tl):
    baseurl = 'http://api.nytimes.com/svc/books/v3/lists/'
    endurl = '.json?api-key=ed91070ee5df688636a455cb3ad9cb72%3A2%3A71777620'     
    url = baseurl + str(date.year) + '-' + date.strftime('%m') + '-' + date.strftime('%d') + '/' + tl + endurl
    l = requests.get(url)
    k = 0
    while l.status_code != 200 and k < 10:
        l = requests.get(url)
        k += 1
    if l.status_code != 200:
        return ''
    return l.json()

In [287]:
#get_list(date, hf)

In [52]:
def get_best(hf, date):
    ybest = {}
    for i in range(52*6):
        l= get_list(date, hf)
        if len(l) > 0:
            ybest[date.strftime('%y-%m-%d')] = l['results']['books']
        date = date + timedelta(days=7)
    return ybest

In [55]:
#pickle.dump(ybest, open('ybest.p', 'wb'))
#ybest= pickle.load( open('ybest.p', 'rb'))


In [14]:
def get_wikilist(wiki, nm, wiurl):
    ''' this function takes t, he text of wikipedia and return a list composed 
    of the date of the awards or bibliography '''
    
    aidx = wiki.find('id="' + nm)
    if aidx == -1 and nm == 'Bibliography':
        match = re.search('id=".*[Ww]orks', wiki)
        widx = 0
        if match != None:
            widx = match.start()
        pidx = wiki.find('id="Publish')
        bidx = wiki.find('id="Books')
        nidx = wiki.find('id="Novels')
        aidx = widx + pidx + bidx + nidx
    if aidx == -1 and nm == 'Awards':
        match = re.search('[Pp]rize', wiki)
        
    aw = wiki[aidx:wiki.find('<h2>', aidx)]
    award = re.findall('<td.*>(.+)</td>', aw) + re.findall('<td>(.+)</td>', aw) + re.findall('<li>(.+)</li>', aw) + \
    re.findall('<dt>(.+)</dt>', aw) 
    if len(award) == 0 and nm == 'Bibliography':
        biurl = wiurl + '_bibliography'
        b = requests.get(biurl)
        if b.status_code == 404:
            return -1
        else:
            bibli = b.text
            aidx = bibli.find('id="Bibliography')
            aw = bibli[aidx:bibli.find('<h2>', aidx)]
            award = re.findall('<td>(.+)</td>', aw) + re.findall('<td.*>(.+)</td>', aw)+ \
            re.findall('<li>(.+)</li>', aw) + re.findall('<dt>(.+)</dt>', aw) 
            re.findall('<dt>(.+)</dt>', aw)
    elif len(award) == 0:
        return -1
    date = []
    for i in award:
        d = re.findall('[0-9]{4}', i)    
        if len(d) > 1:
            d = [d[0]]
        if len(d) > 0:        
            if d[0][0:2] != '19' and d[0][0:2] != '20':
                continue
            date.append(d[0])
    if len(date) == 0:
        return len(award)
    return len(date)

Find some info about the author and the number of published book and awards on wikipedia

In [15]:
def get_genre(wiki, genre):
    out = []
    for i in genre:
        if i in wiki:
            out.append(i)
    return out

In [16]:
basewi = 'http://en.wikipedia.org/wiki/'
def wikiscrape(basewi, onebook, female, male, genre):
    author = onebook['author']
    author = author.encode('utf-8')
    firstname = re.findall('\w+',author)[0]
    if firstname.lower() in female:
        g = 'F'
    elif firstname.lower() in male:
        g = 'M'
    else:
        g = '?'
    onebook['gender'] = g
    if len(re.findall('\w+',author)) > 2:
        author = re.findall('\w+',author)[0] + '_' + re.findall('\w+',author)[1]      
    author = author.replace(' ', '_')
    wiurl  = basewi + author
    w      = requests.get(wiurl)
    wiki   = w.text
    if wiki.find('Disambiguation icon') != -1:
        wiurl  = basewi + author + '_author'
        w      = requests.get(wiurl)
        wiki   = w.text
    if wiki.find('Wikipedia does not have an article with this exact name') != -1:
        onebook['genre'] = ''
        onebook['biblio'] = ''
        onebook['awards'] = ''
        onebook['age'] = ''
        onebook['country'] = ''
        return onebook
    blurb = re.findall('<p>(.+)</p>', wiki)[0]
    onebook['genre'] = get_genre(blurb, genre)
    onebook['biblio'] = get_wikilist(wiki, 'Bibliography', wiurl)
    onebook['awards'] = get_wikilist(wiki, 'Awards', wiurl)
    a = re.findall('class="bday"(.+)-', wiki)
    if len(a) > 0:
        a = re.findall('[0-9]{4}', a[0])[0]
        onebook['age'] = str(datetime.now().year - int(a.decode('utf8')))
    else:
        soup = BeautifulSoup(wiki)
        t = soup.find('table')
        if t != None:
            a = re.findall('[0-9]{4}', t.text)
            if len(a) > 0:
                a = a[0]
                if len(a) > 0:
                    onebook['age'] = str(datetime.now().year - int(a.decode('utf8')))
            else:
                onebook['age'] =''
        else:
            onebook['age'] =''
    c = re.findall('<td class="category".*>(.+)</td>', wiki)
    if len(c) > 0:
        country = c[0].encode('utf8').lower()
        usa = 'united states, america, american, us, u.s., usa, u.s.a'
        if usa.find(country) != -1:
            country = 'USA'
        onebook['country'] = country
    else:
        onebook['country'] = ''
    return onebook

In [124]:
#m = ybest['14-01-01']
#best = [wikiscrape(basewi, x, female, male) for x in m]
#wikiscrape(basewi, m[10], female, male, genre)


In [58]:
def get_author_info(ybest):
    best = {}
    for k in ybest.keys():
        print k
        if len(ybest[k]) > 0:
            best[k] = [wikiscrape(basewi, x, female, male, genre) for x in ybest[k]]
    return best

In [53]:
bookList = {}
for i in bestlist:
    hf = urllib.quote(i)
    startDate = "01/01/09"
    date = datetime.strptime(startDate, "%m/%d/%y")
    ybest = get_best(hf, date)
    best = get_author_info(ybest)
    booklist[hf] = best

2009-01-08 00:00:00
2009-01-15 00:00:00
2009-01-22 00:00:00
2009-01-29 00:00:00
2009-02-05 00:00:00
2009-02-12 00:00:00
2009-02-19 00:00:00
2009-02-26 00:00:00
2009-03-05 00:00:00
2009-03-12 00:00:00
2009-03-19 00:00:00
2009-03-26 00:00:00
2009-04-02 00:00:00
2009-04-09 00:00:00
2009-04-16 00:00:00
2009-04-23 00:00:00
2009-04-30 00:00:00
2009-05-07 00:00:00
2009-05-14 00:00:00
2009-05-21 00:00:00
2009-05-28 00:00:00
2009-06-04 00:00:00
2009-06-11 00:00:00
2009-06-18 00:00:00
2009-06-25 00:00:00
2009-07-02 00:00:00
2009-07-09 00:00:00
2009-07-16 00:00:00
2009-07-23 00:00:00
2009-07-30 00:00:00
2009-08-06 00:00:00
2009-08-13 00:00:00
2009-08-20 00:00:00
2009-08-27 00:00:00
2009-09-03 00:00:00
2009-09-10 00:00:00
2009-09-17 00:00:00
2009-09-24 00:00:00
2009-10-01 00:00:00
2009-10-08 00:00:00
2009-10-15 00:00:00
2009-10-22 00:00:00
2009-10-29 00:00:00
2009-11-05 00:00:00
2009-11-12 00:00:00
2009-11-19 00:00:00
2009-11-26 00:00:00
2009-12-03 00:00:00
2009-12-10 00:00:00
2009-12-17 00:00:00


In [62]:
i = bestlist[1]
hf = urllib.quote(i)
startDate = "01/01/09"
date = datetime.strptime(startDate, "%m/%d/%y")
ybest = get_best(hf, date)
#best = get_author_info(ybest)


TypeError: list indices must be integers, not str

In [56]:
pickle.dump(best, open('best.p', 'wb'))
#best= pickle.load( open('best.p', 'rb'))

Get the data in a dataframe

In [96]:
k = 0
for i in best.keys():
    b = best[i]
    for j in range(nbook):
        v = b[j].values()
        v.insert(0,i)
        v = [x.encode('utf-8') if type(x) == 'str' else x for x in v ]
        v2 = ['' if type(x) == list else x for x in v ]
        df.loc[k] = v2
        k += 1
#print df.head()

In [61]:
pickle.dump(df, open('df.p', 'wb'))
#ybest= pickle.load( open('ybest.p', 'rb'))


In [99]:

df['ntitleword'] = [len(re.findall('\w+', x)) for x in df['title']]

In [57]:
best

{'09-01-01': [{'age': '51',
   u'age_group': u'',
   u'amazon_product_url': u'http://www.amazon.com/The-Christmas-Sweater-Picture-Book/dp/1416995439?tag=thenewyorktim-20',
   u'article_chapter_link': u'',
   u'asterisk': 0,
   u'author': u'Glenn Beck with Kevin Balfe and Jason Wright',
   'awards': -1,
   'biblio': -1,
   u'book_image': u'http://du.ec2.nytimes.com.s3.amazonaws.com/prd/books/9781416594857.jpg',
   u'book_review_link': u'',
   u'contributor': u'by Glenn Beck with Kevin Balfe and Jason Wright.',
   u'contributor_note': u'',
   'country': 'USA',
   u'dagger': 0,
   u'description': u'A boy learns from his disappointment with his mother\u2019s gift.',
   u'first_chapter_link': u'',
   'gender': 'M',
   'genre': [],
   u'isbns': [{u'isbn10': u'141659485X', u'isbn13': u'9781416594857'},
    {u'isbn10': u'1416595007', u'isbn13': u'9781416595007'},
    {u'isbn10': u'1416995439', u'isbn13': u'9781416995432'}],
   u'price': 19.99,
   u'primary_isbn10': u'141659485X',
   u'primary_

In [113]:
#hasreview = [0 if 
df['amazon_product_url'] != ''



0       True
1       True
2       True
3       True
4       True
5       True
6       True
7       True
8       True
9       True
10      True
11      True
12      True
13      True
14      True
15      True
16      True
17      True
18      True
19      True
20      True
21      True
22      True
23      True
24      True
25      True
26      True
27      True
28      True
29      True
        ... 
6550    True
6551    True
6552    True
6553    True
6554    True
6555    True
6556    True
6557    True
6558    True
6559    True
6560    True
6561    True
6562    True
6563    True
6564    True
6565    True
6566    True
6567    True
6568    True
6569    True
6570    True
6571    True
6572    True
6573    True
6574    True
6575    True
6576    True
6577    True
6578    True
6579    True
Name: amazon_product_url, dtype: bool

get all the reviews of the year

In [255]:
r = requests.get('http://api.nytimes.com/svc/search/v2/articlesearch.json?q=books+review&begin_date=20140101&end_date=20141231&api-key=38477d93e711afb3260ca02fcd5b1cdb%3A12%3A71777620')
rjson = r.json()

In [258]:
len(rjson)
rjson

{u'copyright': u'Copyright (c) 2013 The New York Times Company.  All Rights Reserved.',
 u'response': {u'docs': [{u'_id': u'53fbb76479881038210a164a',
    u'abstract': u'Martin Filler acknowledged a significant error in a New York Review of Books article he wrote that was harshly critical of Ms. Hadid.',
    u'blog': [],
    u'byline': {u'original': u'By ALLAN KOZINN',
     u'person': [{u'firstname': u'Allan',
       u'lastname': u'KOZINN',
       u'organization': u'',
       u'rank': 1,
       u'role': u'reported'}]},
    u'document_type': u'blogpost',
    u'headline': {u'kicker': u'ArtsBeat',
     u'main': u'Architecture Critic Acknowledges a Mistake in Critique of Zaha Hadid',
     u'print_headline': u'Architect&#8217;s Lawsuit Elicits Apology'},
    u'keywords': [{u'name': u'persons',
      u'rank': u'1',
      u'value': u'Filler, Martin'},
     {u'name': u'persons', u'rank': u'2', u'value': u'Hadid, Zaha'},
     {u'name': u'organizations',
      u'rank': u'1',
      u'value': u'Ne